In [ ]:
import torch
import torchvision
from PIL import Image

# Create a vector of zeros of size 5
size = (128, 128)
transform = torchvision.transforms.Compose([torchvision.transforms.Resize(size), torchvision.transforms.ToTensor()])
train_dataset = list(torchvision.datasets.Flowers102("/tmp/flowers", "train", transform=transform, download=True))
test_dataset = list(torchvision.datasets.Flowers102("/tmp/flowers", "test", transform=transform, download=True))


def visualize_image(img: torch.Tensor) -> Image.Image:
    return Image.fromarray((img.permute(1, 2, 0) * 255).to(torch.uint8).numpy())


visualize_image(train_dataset[1][0])

In [ ]:
import matplotlib.pyplot as plt

f, ax = plt.subplots(4, 10)
for i, (im, lbl) in enumerate(list(train_dataset)[:40]):
    ax[i // 10, i % 10].imshow(visualize_image(im))
    ax[i // 10, i % 10].set_title(lbl)

class_01 = list(train_dataset)[:20]

## Nearest Neighbor Classifier

$f: \mathbb{R} \to \{0, 1\}$

- Input $x$
- Find *closest* data point $(\tilde x, lbl) \in \mathcal{D}$ in dataset $\mathcal{D}$
- Return its label $lbl$

In [ ]:
def nn_classifier(x):
    dist = [((x - im).pow(2).sum(), lbl) for im, lbl in class_01]
    return min(dist)[1]


nn_classifier(test_dataset[0][0])
accuracy = sum(nn_classifier(x) == lbl for x, lbl in list(test_dataset)[:20]) / 20

In [ ]:
[lbl for _, lbl in list(test_dataset)[:20]]

## K Nearest Neighbor Classifier

$f: \mathbb{R} \to \{0, 1\}$

- Input $x$
- Find k *closest* data points in dataset $\mathcal{D}$
- Return most common label

In [ ]:
def knn_classifier(x, k=3):
    dist = [((x - im).pow(2).sum(), lbl) for im, lbl in class_01]
    k_closest = [lbl for _, lbl in sorted(dist)[:k]]
    return sorted(k_closest)[k // 2]


knn_classifier(test_dataset[3][0])
accuracy = sum(knn_classifier(x) == lbl for x, lbl in list(test_dataset)[:20]) / 20
print(accuracy)

## K Nearest Neighbor Regression

$f: \mathbb{R} \to \mathbb{R}$

- Input $x$
- Find k *closest* data points in dataset $\mathcal{D}$
- Return average value

In [ ]:
def knn_regression(x, k=3):
    dist = [((x - im).pow(2).sum(), lbl) for im, lbl in class_01]
    k_closest = [lbl for _, lbl in sorted(dist)[:k]]
    return torch.mean(torch.tensor(k_closest).float())


knn_regression(test_dataset[3][0])